# Анализ пространственных данных. Домашнее задание №2

Мягкий дедлайн: __4 ноября 2020 г. 23:59__

Жесткий дедлайн (со штрафом в _50%_ от количества набранных вами за ДЗ баллов): __5 ноября 2020 г. 08:59__

Визуализация "чего-либо" __без__ выполненного основного задания оценивается в __0 баллов__

ФИО: `Закладний Антон Владимирович`

Группа: `DS-32`

## Задание №1. Горячая точка (алгоритм - 10 баллов, визуализация - 10 баллов).

Генерируйте рандомные точки на планете Земля до тех пор, пока не попадете на территорию ``Афганистана``

1. Вы можете использовать функции принадлжености точки полигону и расстояния от точки до полигона (в метрах)
2. Предложите не наивный алгоритм поиска (генерировать __напрямую__ точку из полигона границ Афганистана __запрещено__)

In [51]:
import folium
import random
import geopandas as gpd
import pandas as pd
import earthpy as et
import shapely
import datetime

from folium import plugins
from haversine import haversine
from math import degrees

In [4]:
world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))

afghanistan_polygon = world[world['name'] == 'Afghanistan']['geometry'].values[0]

center_polygon_afganistan = afghanistan_polygon.centroid.coords[0][::-1]

In [20]:
def is_dot_in_polygon(lat, lon):
    return shapely.geometry.Point(lon, lat).within(afghanistan_polygon)

In [58]:
def dist(lat, lon):
    return haversine((lat, lon), center_polygon_afganistan)

## Случайный поиск

In [38]:
def random_search(format_lat_lon=True):
    in_polygon = False
    path = []
    count = 0
    while in_polygon == False:
        lat = random.uniform(-90, 90)
        lon = random.uniform(-180, 180)
        in_polygon = is_dot_in_polygon(lat, lon)
        count += 1
        if format_lat_lon:
            path.append([lat, lon])
        else:
            path.append([lon, lat])
    if format_lat_lon:
        print("Точка с координатами ({}, {}) найдена за {} итераций(и)".format(round(lat, 5), round(lon, 5), count))
    else:
        print("Точка с координатами ({}, {}) найдена за {} итераций(и)".format(round(lon, 5), round(lat, 5), count))
    return path

In [45]:
def show_path(path, real_time=False):
    map_ = folium.Map(location=list(center_polygon_afganistan), zoom_start = 2)
    if real_time:
        base_date = datetime.datetime.today()
        features = []
        for i, point in enumerate(path[:-1]):
            base_date += datetime.timedelta(hours=1)
            features.append(
                {
                    'type': 'Feature',
                    'geometry': 
                    {
                        'type': 'Point',
                        'coordinates': point[::-1],
                    },
                    'properties': 
                    {
                        'times': [base_date.strftime("%Y-%m-%d %H:%M:%S")],
                        'icon':'circle',
                    }
                }
            )
        base_date += datetime.timedelta(hours=1)
        features.append(
                {
                    'type': 'Feature',
                    'geometry': 
                    {
                        'type': 'Point',
                        'coordinates': path[-1][::-1],
                    },
                    'properties': 
                    {
                        'times': [base_date.strftime("%Y-%m-%d %H:%M:%S")],
                    }
                }
            )
        folium.plugins.TimestampedGeoJson(
            {
                'type': 'FeatureCollection',
                'features': features,
            }, period='PT1H', auto_play=False, loop=False).add_to(map_)

    else:
        for point in path[:-1]:
            folium.CircleMarker(location=point, 
                                radius = 5, 
                                fill_color="green", 
                                color="gray", 
                                fill_opacity = 0.9).add_to(map_)
        folium.CircleMarker(location=path[-1], 
                            radius = 5, 
                            popup="Afganistan",
                            fill_color="red", 
                            color="gray", 
                            fill_opacity = 0.9).add_to(map_)

    return map_

## Визуализация случайного поиска

In [49]:
path_random = random_search()

Точка с координатами (33.52418, 65.56254) найдена за 696 итераций(и)


In [50]:
show_path(path_random, real_time=False)

## Не случайный поиск

In [114]:
def pair_find():
    
    print('Поиск координат:\n')
    Rzem = 6371
    
    lat = random.uniform(-90, 90)
    lon = random.uniform(-180, 180)

    point_in_polygon = is_dot_in_polygon(lat, lon)
    range_to_point = dist(lat, lon)
    print('Дальность до полигона = {} км'.format(round(range_to_point, 3)))      
    
    path = [[lat, lon]]
    angle_last = 180
    while point_in_polygon == False:
        angle = degrees(range_to_point / Rzem)
        "Обход возможных граничных случаев"
        if angle >= angle_last:
            return pair_find()
        angle_last = angle
        
        lon_r = lon + angle
        lon_l = lon - angle
        if lon_r >= 180:
            lon_r = 179.999
        if lon_l <= -180:
            lon_l = -179.999
        new_lon = [lon_l, lon_r]
        
        dist_ = []
        for i in range(2):
            path.append([lat, new_lon[i]])
            point_in_polygon = is_dot_in_polygon(lat, new_lon[i])
            dist_.append(dist(lat, new_lon[i])) 
            if point_in_polygon:
                lon = new_lon[i]
                print('\nРасчёт окончен!\n')
                print('Точка ({}, {}), дальность = {} км'.format(round(lat, 5), round(lon, 5), round(dist_[i], 3)))
                return path
        
        range_to_point = min(dist_)
        print('Дальность до полигона = {} км'.format(round(range_to_point, 3))) 
        index_lon = dist_.index(range_to_point)
        lon = new_lon[index_lon]
        
        angle = degrees(range_to_point / Rzem)
        lat_r = lat + angle
        lat_l = lat - angle
        if lat_r >= 90:
            lat_r = 89.999
        if lat_l <= -90:
            lat_l = -89.999
        
        new_lat = [lat_l, lat_r]
        
        dist_ = []
        for i in range(2):
            path.append([new_lat[i], lon])
            point_in_polygon = is_dot_in_polygon(new_lat[i], lon)
            dist_.append(dist(new_lat[i], lon)) 
            if point_in_polygon:
                lat = new_lat[i]
                print('\nРасчёт окончен!\n')
                print('Точка ({}, {}), дальность = {} км'.format(round(lat, 5), round(lon, 5), round(dist_[i], 3)))
                #print('Широта =', lat ,'Долгота =', lon, 'Дальность =', dist_[i])
                return path
        range_to_point = min(dist_)
        print('Дальность до полигона = {} км'.format(round(range_to_point, 3))) 
        index_lat = dist_.index(range_to_point)
        lat = new_lat[index_lat]
    return path

In [115]:
path = pair_find()

Поиск координат:

Дальность до полигона = 10643.495 км
Дальность до полигона = 2322.656 км
Дальность до полигона = 2500.258 км
Дальность до полигона = 1604.965 км

Расчёт окончен!

Точка (33.84785, 65.42269), дальность = 61.324 км


In [116]:
show_path(path, real_time=True)

Визуализируйте пошагово предложенный алгоритм при помощи ``Folium``

## Задание №2. Качество жизни (20 баллов).

Для измерения показателя качества жизни в точке, найденной в предыдущем задании, вам необходимо рассчитать следующую сумму расстояний (в метрах):

1. Расстояние от точки до 5 ближайших __*__ банкоматов, находящихся в стране с наибольшим количеством объектов жилой недвижимости
2. Расстояние от точки до 5 ближайших школ, находящихся в стране с наибольшим количеством аптек в столице
3. Расстояние от точки до 5 ближайших кинотеатров, наодящихся в стране с самым большим отношением числа железнодорожных станций к автобусным остановкам в южной части __**__

__*__ При поиске _N_ ближайших объектов обязательно использовать ``R-tree``

__**__ Южной частью страны является территория, находящаяся к югу от множества точек, равноудаленных от самой северной и самой южной точек страны

## Задание №3. Поездка по Нью-Йорку (маршрут - 20 баллов, визуализация - 10 баллов).

Добраться __на автомобиле__ от входа в ``Central Park`` __Нью-Йорка__ (со стороны ``5th Avenue``) до пересечения ``Water Street`` и ``Washington Street`` в Бруклине (откуда получаются лучшие фото Манхэттенского моста) довольно непросто - разумеется, из-за вечных пробок. Однако еще сложнее это сделать, проезжая мимо школ, где дети то и дело переходят дорогу в неположенном месте.

Вам необходимо построить описанный выше маршрут, избегая на своем пути школы. Визуализируйте данный маршрут (также добавив школы и недоступные для проезда участки дорог) при помощи ``Folium``

Данные о расположении школ Нью-Йорка можно найти [здесь](https://catalog.data.gov/dataset/2019-2020-school-point-locations)

In [119]:
from folium import plugins
from folium.plugins import MarkerCluster
from openrouteservice import client

In [121]:
data_school = pd.read_csv("2019_-_2020_School_Point_Locations.csv")

COORD_FROM = [40.797, -73.96068][::-1]
COORD_TO = [40.7032, -73.98975][::-1]

DIRECTION_PARAMS = {'coordinates': [COORD_FROM, COORD_TO],
                    'profile': 'driving-car', 
                    'format_out': 'geojson',
                    'preference': 'shortest',
                    'geometry': 'true',
                   }

api_key = '5b3ce3597851110001cf6248e4b150366d8c4617977c464ac68ecc94'

clnt = client.Client(key=api_key) 

In [135]:
def convert_str_to_lon_lat(str_point):
    list_ = str_point.split(" ")
    return  [float(list_[1].strip('(')), float(list_[2].strip(')'))]


def convert_str_to_lat_lon(str_point):
    list_ = str_point.split(" ")
    return  [float(list_[2].strip(')')), float(list_[1].strip('('))]


def style_function(color, opacity, weight):
    return lambda feature: dict(color=color, opacity=opacity, weight=weight)


def get_regular_route():
    regular_route = clnt.directions(**DIRECTION_PARAMS) # Direction request
    duration, distance = regular_route['features'][0]['properties']['summary'].values()
    return regular_route


def show_path_route(regular_route, map_, color_path='blue', opacity=0.5, weight=4):
    gj= folium.GeoJson(regular_route, name='Regular Route', style_function=style_function(color_path, opacity, weight)).add_to(map_)
    folium.Marker(list(reversed(COORD_FROM)), popup='Central Park').add_to(map_)
    folium.Marker(list(reversed(COORD_TO)), popup='Water Street&Washington Street').add_to(map_)
    return map_


def get_instruction(regular_route):
    data = regular_route['features'][0]['properties']['segments'][0]['steps']
    out = {'name': [], 'instruction': []}
    for row in data:
        out['name'].append(row['name'])
        out['instruction'].append(row['instruction'])
    return out

## Создание карты

In [136]:
base_point = data_school['the_geom'][0]

map_school = folium.Map(location=convert_str_to_lat_lon(base_point), zoom_start = 12)

marker_cluster_school = MarkerCluster().add_to(map_school)

for point in data_school['the_geom']:
    folium.CircleMarker(location=convert_str_to_lat_lon(point), 
                        radius = 9,
                        fill_color= 'white',
                        color='black', 
                        fill_opacity = 0.9).add_to(marker_cluster_school)#add_to(map_school)


## Маршрут между точками

In [137]:
regular_route = get_regular_route()

get_instruction(regular_route)

{'name': ['Central Park West',
  '86th Street Transverse Road',
  '5th Avenue',
  '5th Avenue',
  'East 18th Street',
  'Park Avenue South',
  'East 10th Street',
  '3rd Avenue',
  'Manhattan Bridge',
  '-',
  'Sands Street',
  'Water Street',
  '-'],
 'instruction': ['Head southwest on Central Park West',
  'Turn left onto 86th Street Transverse Road',
  'Turn right onto 5th Avenue',
  'Keep left onto 5th Avenue',
  'Turn left onto East 18th Street',
  'Turn right onto Park Avenue South',
  'Turn left onto East 10th Street',
  'Turn right onto 3rd Avenue',
  'Keep left onto Manhattan Bridge',
  'Keep right',
  'Turn left onto Sands Street',
  'Turn left onto Water Street',
  'Arrive at Water Street, straight ahead']}

In [138]:
show_path_route(regular_route, map_school, opacity=1)

In [142]:
def create_buffer_polygon(point, resolution=10, radius=1):       
    return shapely.geometry.Point(convert_str_to_lon_lat(point)).buffer(radius, resolution=resolution)


def get_polygons_school(resolution=2, radius=0.0008):
    poligons = []
    for point in data_school['the_geom']:
        poligons.append(create_buffer_polygon(point, resolution=resolution, radius=radius))
    return poligons


def add_polygons_in_map(map_, list_poligons, color='black', fill_color='#ffd699', weight=1):
    for poligon in list_poligons:
        revers_data = list(map(lambda x: x[::-1], poligon.exterior.coords))
        folium.vector_layers.Polygon(locations=revers_data,
                                      color=color,
                                      fill_color=fill_color,
                                      fill_opacity=0.2,
                                      weight=weight).add_to(map_)
    return map_

## Построение полигонов ограничивающих зону школ

In [141]:
polygons_school = get_poligons_school(resolution=2, radius=0.0008)

In [144]:
add_polygons_in_map(map_school, polygons_school)

In [145]:
def get_list_intersects(route_buffer, list_poligons):
    sites_buffer_poly = []
    for poligons in list_poligons:
        poly = shapely.geometry.Polygon(poligons)
        if route_buffer.intersects(poly):
            sites_buffer_poly.append(poly)
    return sites_buffer_poly


def get_new_path(regular_route, poligons_school):
    route_buffer = shapely.geometry.LineString(regular_route['features'][0]['geometry']['coordinates'])
    list_intersects_school = get_list_intersects(route_buffer, poligons_school)
    request_params = dict(DIRECTION_PARAMS)
    count = 0
    
    list_full_intersects = []
    list_intersects = [list_intersects_school]
    list_route_detour = []
#     Поиск маршрута до тех пор пока не будет пересечений с полигонами школ, если пересечение произошло, 
#     то эти полигоны добавляются в 'avoid_polygons' для учета в следующем маршруте
    while list_intersects_school:
        count  += 1
        print('Изменение пути №',count, 'Число школ на пути = ', len(list_intersects_school))
        list_full_intersects +=list_intersects_school
        
        request_params['options'] = {'avoid_polygons': shapely.geometry.mapping(
            shapely.geometry.MultiPolygon(list_full_intersects))}
        route_detour = clnt.directions(**request_params)
        
        list_route_detour.append(route_detour)
        route_buffer = shapely.geometry.LineString(route_detour['features'][0]['geometry']['coordinates'])
        list_intersects_school = get_list_intersects(route_buffer, poligons_school)
        list_intersects.append(list_intersects_school)
    return list_route_detour, list_intersects


def show_all_path_detour(route_detour, list_intersects, map_):
    list_color = ['green','black','orange','brown','pink','purple'] 
    for i, detour in enumerate(route_detour[:-1]):
        show_path_route(detour, map_, color_path=list_color[i%len(list_color)], weight = 3, opacity=1)
        add_poligons_in_map(map_, list_intersects[i], fill_color=list_color[i%len(list_color)], weight=3)
#     Для финального объездного пути
    show_path_route(route_detour[i+1], map_, color_path='red', opacity=1)
    return map_

## Поиск обходных маршрутов

In [146]:
route_detour, list_intersects = get_new_path(regular_route, polygons_school)

Изменение пути № 1 Число школ на пути =  4
Изменение пути № 2 Число школ на пути =  3
Изменение пути № 3 Число школ на пути =  4
Изменение пути № 4 Число школ на пути =  2
Изменение пути № 5 Число школ на пути =  8


In [147]:
map_school

In [160]:
maps = []
for i, route in enumerate(route_detour):
    maps.append(folium.Map(location=convert_str_to_lat_lon(base_point), zoom_start = 12))
    show_path_route(route, maps[-1], color_path='green')
    add_poligons_in_map(maps[-1], list_intersects[i+1], color='black', fill_color='black', weight=2)

In [161]:
maps[0]

In [162]:
maps[1]

In [163]:
maps[2]

In [164]:
maps[3]

In [165]:
maps[4]